Epocs = 40, dataset 3000 

In [1]:
import pandas as pd
import glob
import numpy
import csv
from nltk.tokenize import word_tokenize
import xlrd
import re
from nltk import bigrams
from nltk import ngrams
import operator
from collections import Counter
from nltk.corpus import stopwords
import string
import matplotlib.pyplot as plt

In [2]:
from random import randint
from numpy import array
from numpy import argmax
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [3]:
path = r'E:\Level 4 Project\dataset\final\preprocess' # use your path
all_files = glob.glob(path + "/*.csv")

In [4]:
li = []

In [5]:
for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

In [6]:
df = pd.concat(li, axis=0, ignore_index=True, sort=False)

In [7]:
df.head()

Date  \
0  2014-01-01 23:59:47+00:00    
1  2014-01-01 23:57:47+00:00    
2  2014-01-01 23:56:21+00:00    
3  2014-01-01 23:56:03+00:00    
4  2014-01-01 23:55:55+00:00    

                                               Tweet  
0   Clearwater Beach,FL Scattered Thunderstorms t...  
1   Tourism disappeared because of Troubles: To...  
2   I'm at Department of Tourism and Hospitality ...  
3   'Like a Napa Valley wine tour': Pot tourism r...  
4           Focus : Recreation & Tourism Planning .

In [8]:
df.shape

(5492006, 2)

In [9]:
emoticons_str = r"""
    (?:
        [:=;] # Eyes
        [oO\-]? # Nose (optional)
        [D\)\]\(\]/\\OpP] # Mouth
    )"""

In [10]:
def preprocess_fornothash(s, lowercase=True):
    tokens = tokenize_fornothash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_fornothash(s):
    return tokens_re_fornothash.findall(s)


regex_str_fornothash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    #r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_fornothash = re.compile(r'(' + '|'.join(regex_str_fornothash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [11]:
def preprocess_forhash(s, lowercase=True):
    tokens = tokenize_forhash(s)
    if lowercase:
        tokens = [token if emoticon_re.search(token) else token.lower() for token in tokens]
    return tokens

def tokenize_forhash(s):
    return tokens_re_forhash.findall(s)

regex_str_forhash = [
    emoticons_str,
    r'<[^>]+>',  # HTML tags
    r'(?:@[\w_]+)',  # @-mentions
    r"(?:\#+[\w_]+[\w\'_\-]*[\w_]+)",  # hash-tags
    r'http[s]?://(?:[a-z]|[0-9]|[$-_@.&amp;+]|[!*\(\),]|(?:%[0-9a-f][0-9a-f]))+',  # URLs

    r'(?:(?:\d+,?)+(?:\.?\d+)?)',  # numbers
    r"(?:[a-z][a-z'\-_]+[a-z])",  # words with - and '
    r'(?:[\w_]+)',  # other words
    r'(?:\S)'  # anything else
]

tokens_re_forhash = re.compile(r'(' + '|'.join(regex_str_forhash) + ')', re.VERBOSE | re.IGNORECASE)
emoticon_re = re.compile(r'^' + emoticons_str + '$', re.VERBOSE | re.IGNORECASE)

In [12]:
punctuation = list(string.punctuation)
unnecssary = ['The','tourism','I','rt', 'via','...','â','click']
unnecssary_hash = ['#','#tourism']
ascii_words = ['\x92','\x96']
years = ['2018','2017','2016','2015','2014','2013']
numbers = ['nine']
stop = stopwords.words('english') + punctuation + unnecssary + ascii_words + years + unnecssary_hash + numbers

count_all = []
popular_common_words = []
i=0
sets=3000

c =0
for x in range(sets):
    count_all.append(Counter())

for y in range(sets):
    for x in range(1, 500):
        value = df.loc[i, "Tweet"]

        #terms_all = [term for term in preprocess_fornothash(value) if term not in stop]  
        terms_all = [term for term in preprocess_forhash(value)
                  if term.startswith('#') if term not in stop]
        i = i + 1
        count_all[y].update(terms_all)
    
    popular_common_words.append(count_all[y].most_common(5))
        

In [13]:
trendingTopicsAll = []

def processTrendingArray(str):
    global trendingTopicsAll
    b = [i for i,x in enumerate(trendingTopicsAll) if x == str]
    if(b == []):
        trendingTopicsAll.append(str)
        return len(trendingTopicsAll)-1
    else:
        return b[0]

In [14]:
trendingTopicsInEachDays = []
trendingIdsInEachDays = []
for index, y in enumerate(popular_common_words):
    trendingTopicsInEachDays.append([])
    trendingIdsInEachDays.append([])
    for x in y:
        trendingTopicsInEachDays[index].append(x[0])
        trendingIdsInEachDays[index].append(processTrendingArray(x[0]))
        

# print(trendingTopicsInEachDays)
# print("####################")
print(trendingTopicsAll)
# print("####################")
# print(trendingIdsInEachDays)

['#travel', '#news', '#amsterdam', '#netherlands', '#holland', '#smtravel', '#trip', '#photo', '#marijuana', '#travelers', '#latestnews', '#street', '#htmi', '#colorado', '#pakistan', '#adventure', '#maldives', '#town', '#road', '#jobs', '#aglasem', '#infografia', '#infographic', '#googlenews', '#webdesign', '#vatican', '#popefrancis', '#business', '#amazing', '#chile', '#ttot', '#hhi', '#cnn', '#culture', '#carrefour', '#muscat', '#egypt', '#blog', '#saveswedenswolves', '#backpacking', '#welcome_to_egypt', '#alanailham', '#thailand', '#vmy2014', '#haiti', '#photography', '#church', '#southafrica', '#qatar', '#malaysia', '#hospitality', '#hotels', '#food', '#neworleanswill', '#cruisepeople', '#ofc14', '#china', '#rwanda', '#ecuador', '#keepwolveslisted', '#nysos14', '#expediachat', '#africa', '#job', '#tech', '#socialmedia', '#mashable', '#gdaytourism', '#ireland', '#hampi', '#uganda', '#scotlandhour', '#twitter', '#marketing', '#talent4hire', '#sayfie', '#ff', '#oman', '#caribbean', '

In [15]:
# generate a sequence of random numbers in [0, 99]
tweetIdsCount = -1
inputs = len(trendingTopicsAll)

def generate_sequence():
    global tweetIdsCount
    print("tweetIdsCount - ",tweetIdsCount)
    tweetIdsCount = tweetIdsCount+1
    return (trendingIdsInEachDays[tweetIdsCount])
    #return [23,12,45]
    
# one hot encode sequence
def one_hot_encode(sequence, n_unique=inputs):
	encoding = list()
	for value in sequence:
		vector = [0 for _ in range(n_unique)]
		vector[value] = 1
		encoding.append(vector)
	return array(encoding)
 
# decode a one hot encoded string
def one_hot_decode(encoded_seq):
	return [argmax(vector) for vector in encoded_seq]
 
# generate data for the lstm
def generate_data():
	# generate sequence
	sequence = generate_sequence()
	# one hot encode
	encoded = one_hot_encode(sequence)
	# convert to 3d for input
	X = encoded.reshape(encoded.shape[0], 1, encoded.shape[1])
	return X, encoded    
    
# define model
model = Sequential() 
model.add(LSTM(50, input_shape=(1, inputs)))
model.add(Dense(inputs, activation='relu'))
model.add(Dense(inputs, activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit model
for i in range(2000):
	X, y = generate_data()
	model.fit(X, y, epochs=40, batch_size=1, verbose=2)
# evaluate model on new data
X, y = generate_data()
yhat = model.predict(X)

#print('Expected:  %s' % one_hot_decode(y))
#print('Predicted: %s' % one_hot_decode(yhat))

a = []
b = []
i = 0;
# for x in range(5):
#     if(one_hot_decode(y)[x] == one_hot_decode(yhat)[x]):
#         i += 1
#     a.append(trendingTopicsAll[one_hot_decode(y)[x]])
#     b.append(trendingTopicsAll[one_hot_decode(yhat)[x]])
   
# print("Expected: ",a)
# print("Predicted: ",b)
# print("Test Accuracy: ",(i/5)*100)

W0117 20:35:35.990697 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:1251: calling VarianceScaling.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


tweetIdsCount -  -1


W0117 20:35:37.530685 15184 deprecation.py:323] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\math_grad.py:1250: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


Epoch 1/40
5/5 - 3s - loss: 7.5672 - acc: 0.0000e+00
Epoch 2/40
5/5 - 0s - loss: 7.5202 - acc: 0.6000
Epoch 3/40
5/5 - 0s - loss: 7.4556 - acc: 0.6000
Epoch 4/40
5/5 - 0s - loss: 7.3564 - acc: 1.0000
Epoch 5/40
5/5 - 0s - loss: 7.1988 - acc: 0.8000
Epoch 6/40
5/5 - 0s - loss: 6.9525 - acc: 0.8000
Epoch 7/40
5/5 - 0s - loss: 6.5796 - acc: 0.8000
Epoch 8/40
5/5 - 0s - loss: 6.0312 - acc: 0.8000
Epoch 9/40
5/5 - 0s - loss: 5.2368 - acc: 0.6000
Epoch 10/40
5/5 - 0s - loss: 4.1321 - acc: 0.6000
Epoch 11/40
5/5 - 0s - loss: 2.8373 - acc: 0.6000
Epoch 12/40
5/5 - 0s - loss: 1.8768 - acc: 0.4000
Epoch 13/40
5/5 - 0s - loss: 1.6028 - acc: 0.4000
Epoch 14/40
5/5 - 0s - loss: 1.5408 - acc: 0.6000
Epoch 15/40
5/5 - 0s - loss: 1.5212 - acc: 0.6000
Epoch 16/40
5/5 - 1s - loss: 1.4932 - acc: 0.8000
Epoch 17/40
5/5 - 1s - loss: 1.4836 - acc: 0.8000
Epoch 18/40
5/5 - 0s - loss: 1.4514 - acc: 0.8000
Epoch 19/40
5/5 - 0s - loss: 1.4174 - acc: 0.8000
Epoch 20/40
5/5 - 0s - loss: 1.3972 - acc: 0.8000
Epoch

5/5 - 0s - loss: 0.1105 - acc: 1.0000
Epoch 5/40
5/5 - 0s - loss: 0.0807 - acc: 1.0000
Epoch 6/40
5/5 - 0s - loss: 0.0466 - acc: 1.0000
Epoch 7/40
5/5 - 0s - loss: 0.0377 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0310 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0226 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0199 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0166 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.0150 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.0133 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0121 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.0107 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.0098 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.0090 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 0.0083 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 0.0075 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 0.0070 - acc: 1.0000
Epoch 21/40
5/5 - 0s - loss: 0.0065 - acc: 1.0000
Epoch 22/40
5/5 - 0s - loss: 0.0060 - acc: 1.0000
Epoch 23/40
5/5 - 0s - loss: 0.0056 - acc: 1.0000
Epoch 24/40
5/5 -

...

5/5 - 0s - loss: 3.1102 - acc: 0.8000
Epoch 2/40
5/5 - 0s - loss: 2.6758 - acc: 0.8000
Epoch 3/40
5/5 - 0s - loss: 1.9962 - acc: 0.8000
Epoch 4/40
5/5 - 0s - loss: 1.5850 - acc: 0.8000
Epoch 5/40
5/5 - 0s - loss: 1.1618 - acc: 0.8000
Epoch 6/40
5/5 - 0s - loss: 0.6679 - acc: 0.8000
Epoch 7/40
5/5 - 0s - loss: 0.1290 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0205 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0079 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0026 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0011 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 9.0996e-04 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 7.4893e-04 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 6.6568e-04 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 5.7977e-04 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 5.5187e-04 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 4.9889e-04 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 4.6741e-04 - acc: 1.0000
Epoch 19/40
5/5 - 0s - loss: 4.5298e-04 - acc: 1.0000
Epoch 20/40
5/5 - 0s - loss: 4.2823e-0

Epoch 39/40
5/5 - 0s - loss: 7.2891e-04 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 6.9336e-04 - acc: 1.0000
tweetIdsCount -  1984
Epoch 1/40
5/5 - 0s - loss: 3.3378 - acc: 0.8000
Epoch 2/40
5/5 - 0s - loss: 2.4787 - acc: 0.8000
Epoch 3/40
5/5 - 0s - loss: 2.0355 - acc: 0.8000
Epoch 4/40
5/5 - 0s - loss: 1.5597 - acc: 0.8000
Epoch 5/40
5/5 - 0s - loss: 0.9973 - acc: 0.8000
Epoch 6/40
5/5 - 0s - loss: 0.4564 - acc: 0.8000
Epoch 7/40
5/5 - 0s - loss: 0.1746 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0340 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0051 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0062 - acc: 1.0000
Epoch 11/40
5/5 - 0s - loss: 0.0064 - acc: 1.0000
Epoch 12/40
5/5 - 0s - loss: 0.0054 - acc: 1.0000
Epoch 13/40
5/5 - 0s - loss: 0.0040 - acc: 1.0000
Epoch 14/40
5/5 - 0s - loss: 0.0034 - acc: 1.0000
Epoch 15/40
5/5 - 0s - loss: 0.0018 - acc: 1.0000
Epoch 16/40
5/5 - 0s - loss: 0.0013 - acc: 1.0000
Epoch 17/40
5/5 - 0s - loss: 0.0012 - acc: 1.0000
Epoch 18/40
5/5 - 0s - loss: 

Epoch 32/40
5/5 - 0s - loss: 7.0917e-05 - acc: 1.0000
Epoch 33/40
5/5 - 0s - loss: 6.9249e-05 - acc: 1.0000
Epoch 34/40
5/5 - 0s - loss: 6.8200e-05 - acc: 1.0000
Epoch 35/40
5/5 - 0s - loss: 6.6603e-05 - acc: 1.0000
Epoch 36/40
5/5 - 0s - loss: 6.5554e-05 - acc: 1.0000
Epoch 37/40
5/5 - 0s - loss: 6.4649e-05 - acc: 1.0000
Epoch 38/40
5/5 - 0s - loss: 6.3981e-05 - acc: 1.0000
Epoch 39/40
5/5 - 0s - loss: 6.3099e-05 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 6.1646e-05 - acc: 1.0000
tweetIdsCount -  1988
Epoch 1/40
5/5 - 0s - loss: 2.8264 - acc: 0.8000
Epoch 2/40
5/5 - 0s - loss: 2.2851 - acc: 0.8000
Epoch 3/40
5/5 - 0s - loss: 1.8430 - acc: 0.8000
Epoch 4/40
5/5 - 0s - loss: 1.1772 - acc: 0.8000
Epoch 5/40
5/5 - 0s - loss: 0.8819 - acc: 0.8000
Epoch 6/40
5/5 - 0s - loss: 0.2641 - acc: 1.0000
Epoch 7/40
5/5 - 0s - loss: 0.0382 - acc: 1.0000
Epoch 8/40
5/5 - 0s - loss: 0.0110 - acc: 1.0000
Epoch 9/40
5/5 - 0s - loss: 0.0022 - acc: 1.0000
Epoch 10/40
5/5 - 0s - loss: 0.0033 - acc: 1.0000
E

Epoch 27/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 29/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 30/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 31/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 32/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 33/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 34/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 35/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 36/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 37/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 38/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 39/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 0.0000e+00 - acc: 1.0000
tweetIdsCount -  1992
Epoch 1/40
5/5 - 0s - loss: 7.3359 - acc: 0.6000
Epoch 2/40
5/5 - 0s - loss: 4.9724 - acc: 0.6000
Epoch 3/40
5/5 - 0s - loss: 3.8513 - acc: 0.6000
Epoch 4/40
5/5 - 0s - loss: 2.9029 - acc: 0.6000
Epoch 5/40
5/5 - 0s - loss

Epoch 23/40
5/5 - 0s - loss: 0.0055 - acc: 1.0000
Epoch 24/40
5/5 - 0s - loss: 0.0050 - acc: 1.0000
Epoch 25/40
5/5 - 0s - loss: 0.0046 - acc: 1.0000
Epoch 26/40
5/5 - 0s - loss: 0.0043 - acc: 1.0000
Epoch 27/40
5/5 - 0s - loss: 0.0039 - acc: 1.0000
Epoch 28/40
5/5 - 0s - loss: 0.0037 - acc: 1.0000
Epoch 29/40
5/5 - 0s - loss: 0.0035 - acc: 1.0000
Epoch 30/40
5/5 - 0s - loss: 0.0033 - acc: 1.0000
Epoch 31/40
5/5 - 0s - loss: 0.0031 - acc: 1.0000
Epoch 32/40
5/5 - 0s - loss: 0.0029 - acc: 1.0000
Epoch 33/40
5/5 - 0s - loss: 0.0027 - acc: 1.0000
Epoch 34/40
5/5 - 0s - loss: 0.0026 - acc: 1.0000
Epoch 35/40
5/5 - 0s - loss: 0.0025 - acc: 1.0000
Epoch 36/40
5/5 - 0s - loss: 0.0023 - acc: 1.0000
Epoch 37/40
5/5 - 0s - loss: 0.0022 - acc: 1.0000
Epoch 38/40
5/5 - 0s - loss: 0.0021 - acc: 1.0000
Epoch 39/40
5/5 - 0s - loss: 0.0020 - acc: 1.0000
Epoch 40/40
5/5 - 0s - loss: 0.0019 - acc: 1.0000
tweetIdsCount -  1996
Epoch 1/40
5/5 - 0s - loss: 3.9627 - acc: 0.6000
Epoch 2/40
5/5 - 0s - loss: 2

In [16]:
print(tweetIdsCount)
testaccuracy = []

def getOneAccuracy(a,b):
    i = 0;
    for x in range(5):
        if(a[x] == b[x]):
            i += 1
    return i/5

def getTestData():
    for i in range(990):
        X, y = generate_data()
        yhat = model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))
    
getTestData()
print(testaccuracy)
print('average - ',sum(testaccuracy) / len(testaccuracy))

2000
tweetIdsCount -  2000
Expected:  [0, 1402, 311, 47, 1407]
Predicted: [0, 1402, 311, 47, 1407]
tweetIdsCount -  2001
Expected:  [0, 1402, 62, 102, 370]
Predicted: [0, 1402, 62, 102, 370]
tweetIdsCount -  2002
Expected:  [0, 132, 730, 1, 1422]
Predicted: [0, 132, 730, 1, 1420]
tweetIdsCount -  2003
Expected:  [0, 1423, 545, 547, 107]
Predicted: [0, 1420, 545, 547, 107]
tweetIdsCount -  2004
Expected:  [0, 545, 107, 730, 1418]
Predicted: [0, 545, 107, 730, 1418]
tweetIdsCount -  2005
Expected:  [0, 107, 730, 311, 780]
Predicted: [0, 107, 730, 311, 780]
tweetIdsCount -  2006
Expected:  [0, 107, 411, 545, 6]
Predicted: [0, 107, 411, 545, 6]
tweetIdsCount -  2007
Expected:  [0, 547, 545, 1424, 730]
Predicted: [0, 547, 545, 1420, 730]
tweetIdsCount -  2008
Expected:  [0, 730, 545, 273, 547]
Predicted: [0, 730, 545, 273, 547]
tweetIdsCount -  2009
Expected:  [0, 730, 36, 602, 516]
Predicted: [0, 730, 36, 602, 516]
tweetIdsCount -  2010
Expected:  [0, 730, 739, 1425, 779]
Predicted: [0, 73

Predicted: [0, 132, 730, 107, 1]
tweetIdsCount -  2094
Expected:  [0, 102, 1472, 101, 663]
Predicted: [0, 102, 1420, 101, 663]
tweetIdsCount -  2095
Expected:  [1473, 0, 132, 730, 1474]
Predicted: [1420, 0, 132, 730, 1420]
tweetIdsCount -  2096
Expected:  [1473, 0, 1472, 730, 1475]
Predicted: [1420, 0, 1420, 730, 1420]
tweetIdsCount -  2097
Expected:  [0, 730, 107, 545, 7]
Predicted: [0, 730, 107, 545, 7]
tweetIdsCount -  2098
Expected:  [0, 730, 7, 107, 134]
Predicted: [0, 730, 7, 107, 134]
tweetIdsCount -  2099
Expected:  [0, 132, 107, 730, 547]
Predicted: [0, 132, 107, 730, 547]
tweetIdsCount -  2100
Expected:  [0, 730, 132, 7, 547]
Predicted: [0, 730, 132, 7, 547]
tweetIdsCount -  2101
Expected:  [0, 730, 545, 107, 547]
Predicted: [0, 730, 545, 107, 547]
tweetIdsCount -  2102
Expected:  [0, 107, 730, 102, 545]
Predicted: [0, 107, 730, 102, 545]
tweetIdsCount -  2103
Expected:  [12, 0, 1, 730, 78]
Predicted: [12, 0, 1, 730, 78]
tweetIdsCount -  2104
Expected:  [0, 990, 1476, 78, 131

Predicted: [0, 730, 1420, 21, 22]
tweetIdsCount -  2190
Expected:  [0, 730, 1523, 1524, 1525]
Predicted: [0, 730, 1417, 1420, 1420]
tweetIdsCount -  2191
Expected:  [0, 730, 1519, 1447, 602]
Predicted: [0, 730, 1420, 1420, 602]
tweetIdsCount -  2192
Expected:  [0, 1519, 730, 27, 1]
Predicted: [0, 1420, 730, 27, 1]
tweetIdsCount -  2193
Expected:  [0, 1519, 1447, 730, 66]
Predicted: [0, 1420, 1420, 730, 66]
tweetIdsCount -  2194
Expected:  [0, 311, 1519, 814, 780]
Predicted: [0, 311, 1420, 814, 780]
tweetIdsCount -  2195
Expected:  [0, 1519, 62, 730, 1338]
Predicted: [0, 1420, 62, 730, 1420]
tweetIdsCount -  2196
Expected:  [0, 1526, 1510, 1396, 33]
Predicted: [0, 1420, 1417, 1420, 33]
tweetIdsCount -  2197
Expected:  [0, 730, 1519, 80, 50]
Predicted: [0, 730, 1420, 80, 50]
tweetIdsCount -  2198
Expected:  [0, 730, 1519, 1, 1447]
Predicted: [0, 730, 1420, 1, 1420]
tweetIdsCount -  2199
Expected:  [0, 1447, 45, 602, 1519]
Predicted: [0, 1420, 45, 602, 1420]
tweetIdsCount -  2200
Expected

Expected:  [1434, 0, 1558, 1559, 730]
Predicted: [1417, 0, 1420, 1420, 730]
tweetIdsCount -  2290
Expected:  [0, 730, 102, 50, 656]
Predicted: [0, 730, 102, 50, 1082]
tweetIdsCount -  2291
Expected:  [0, 1560, 730, 833, 134]
Predicted: [0, 1417, 730, 833, 134]
tweetIdsCount -  2292
Expected:  [0, 730, 30, 21, 794]
Predicted: [0, 730, 30, 21, 794]
tweetIdsCount -  2293
Expected:  [0, 730, 1560, 132, 921]
Predicted: [0, 730, 1417, 132, 921]
tweetIdsCount -  2294
Expected:  [0, 730, 45, 239, 833]
Predicted: [0, 730, 45, 239, 833]
tweetIdsCount -  2295
Expected:  [0, 1447, 730, 45, 219]
Predicted: [0, 1420, 730, 45, 1132]
tweetIdsCount -  2296
Expected:  [0, 643, 1, 730, 650]
Predicted: [0, 643, 1, 730, 1420]
tweetIdsCount -  2297
Expected:  [0, 730, 1519, 1561, 162]
Predicted: [0, 730, 1420, 1420, 162]
tweetIdsCount -  2298
Expected:  [0, 730, 1287, 202, 201]
Predicted: [0, 730, 1420, 202, 201]
tweetIdsCount -  2299
Expected:  [0, 602, 134, 6, 833]
Predicted: [0, 602, 134, 6, 833]
tweetId

Predicted: [0, 1420, 730, 1420, 1074]
tweetIdsCount -  2379
Expected:  [0, 730, 734, 1519, 44]
Predicted: [0, 730, 734, 1420, 44]
tweetIdsCount -  2380
Expected:  [0, 1602, 730, 1519, 1]
Predicted: [0, 1420, 730, 1420, 1]
tweetIdsCount -  2381
Expected:  [0, 1602, 730, 1603, 30]
Predicted: [0, 1420, 730, 1420, 30]
tweetIdsCount -  2382
Expected:  [0, 730, 131, 331, 27]
Predicted: [0, 730, 131, 879, 27]
tweetIdsCount -  2383
Expected:  [0, 1597, 607, 1519, 730]
Predicted: [0, 1420, 607, 1420, 730]
tweetIdsCount -  2384
Expected:  [0, 36, 45, 6, 1604]
Predicted: [0, 36, 45, 6, 1420]
tweetIdsCount -  2385
Expected:  [0, 730, 1605, 1606, 30]
Predicted: [0, 730, 1420, 1420, 30]
tweetIdsCount -  2386
Expected:  [0, 934, 730, 1519, 142]
Predicted: [0, 934, 730, 1420, 142]
tweetIdsCount -  2387
Expected:  [0, 1607, 1608, 1609, 134]
Predicted: [0, 1420, 1417, 1420, 134]
tweetIdsCount -  2388
Expected:  [0, 1522, 134, 1, 1594]
Predicted: [0, 1420, 134, 1, 1420]
tweetIdsCount -  2389
Expected:  [

...

Expected:  [0, 734, 1690, 730, 655]
Predicted: [0, 734, 1420, 730, 1420]
tweetIdsCount -  2563
Expected:  [0, 1691, 1692, 1693, 1694]
Predicted: [0, 1420, 1420, 1420, 1420]
tweetIdsCount -  2564
Expected:  [0, 1684, 730, 1695, 44]
Predicted: [0, 1420, 730, 1420, 44]
tweetIdsCount -  2565
Expected:  [0, 1696, 730, 833, 52]
Predicted: [0, 1420, 730, 833, 52]
tweetIdsCount -  2566
Expected:  [215, 0, 730, 1519, 1599]
Predicted: [1420, 0, 730, 1420, 1420]
tweetIdsCount -  2567
Expected:  [0, 215, 116, 1328, 1519]
Predicted: [0, 1420, 116, 1328, 1420]
tweetIdsCount -  2568
Expected:  [0, 1697, 45, 1519, 730]
Predicted: [0, 1420, 45, 1420, 730]
tweetIdsCount -  2569
Expected:  [0, 730, 1698, 1699, 655]
Predicted: [0, 730, 1420, 1420, 1420]
tweetIdsCount -  2570
Expected:  [0, 730, 1699, 1700, 1701]
Predicted: [0, 730, 1420, 1420, 1420]
tweetIdsCount -  2571
Expected:  [0, 1702, 405, 730, 15]
Predicted: [0, 1420, 405, 730, 15]
tweetIdsCount -  2572
Expected:  [0, 730, 713, 176, 56]
Predicted:

Expected:  [87, 1741, 1742, 1744, 1745]
Predicted: [1420, 1420, 1420, 1420, 1420]
tweetIdsCount -  2651
Expected:  [0, 1746, 730, 1741, 1742]
Predicted: [0, 1420, 730, 1420, 1420]
tweetIdsCount -  2652
Expected:  [0, 1746, 88, 73, 1519]
Predicted: [0, 1420, 91, 73, 1420]
tweetIdsCount -  2653
Expected:  [0, 81, 6, 663, 902]
Predicted: [0, 81, 6, 663, 902]
tweetIdsCount -  2654
Expected:  [0, 730, 73, 1519, 1599]
Predicted: [0, 730, 73, 1420, 1420]
tweetIdsCount -  2655
Expected:  [0, 45, 73, 36, 402]
Predicted: [0, 45, 73, 36, 402]
tweetIdsCount -  2656
Expected:  [0, 734, 1747, 1519, 730]
Predicted: [0, 734, 1420, 1420, 730]
tweetIdsCount -  2657
Expected:  [0, 734, 359, 1748, 50]
Predicted: [0, 734, 1420, 1420, 50]
tweetIdsCount -  2658
Expected:  [0, 1602, 730, 359, 49]
Predicted: [0, 1420, 730, 1420, 984]
tweetIdsCount -  2659
Expected:  [0, 566, 74, 1602, 1748]
Predicted: [0, 566, 74, 1420, 1420]
tweetIdsCount -  2660
Expected:  [0, 1749, 81, 696, 1748]
Predicted: [0, 1420, 81, 69

Expected:  [0, 730, 73, 370, 30]
Predicted: [0, 730, 73, 370, 30]
tweetIdsCount -  2743
Expected:  [0, 730, 299, 840, 102]
Predicted: [0, 730, 1390, 108, 102]
tweetIdsCount -  2744
Expected:  [0, 1790, 1791, 713, 73]
Predicted: [0, 1420, 1420, 1420, 73]
tweetIdsCount -  2745
Expected:  [0, 734, 730, 1519, 1599]
Predicted: [0, 734, 730, 1420, 1420]
tweetIdsCount -  2746
Expected:  [0, 311, 1602, 780, 730]
Predicted: [0, 311, 1420, 780, 730]
tweetIdsCount -  2747
Expected:  [0, 1602, 73, 1068, 1792]
Predicted: [0, 1420, 73, 1420, 1420]
tweetIdsCount -  2748
Expected:  [0, 730, 1, 73, 49]
Predicted: [0, 730, 1, 73, 984]
tweetIdsCount -  2749
Expected:  [0, 1519, 730, 1, 1599]
Predicted: [0, 1420, 730, 1, 1420]
tweetIdsCount -  2750
Expected:  [0, 730, 1793, 1794, 1]
Predicted: [0, 730, 1420, 1420, 1]
tweetIdsCount -  2751
Expected:  [1788, 0, 1793, 1794, 730]
Predicted: [1420, 0, 1420, 1420, 730]
tweetIdsCount -  2752
Expected:  [0, 1795, 1519, 219, 73]
Predicted: [0, 1420, 1420, 1132, 73

Expected:  [1837, 0, 73, 730, 1]
Predicted: [1420, 0, 73, 730, 1]
tweetIdsCount -  2839
Expected:  [21, 22, 134, 0, 73]
Predicted: [21, 22, 134, 0, 73]
tweetIdsCount -  2840
Expected:  [0, 64, 1838, 794, 73]
Predicted: [0, 64, 1420, 794, 73]
tweetIdsCount -  2841
Expected:  [0, 734, 36, 1839, 45]
Predicted: [0, 734, 36, 1420, 45]
tweetIdsCount -  2842
Expected:  [0, 311, 780, 73, 19]
Predicted: [0, 311, 780, 73, 19]
tweetIdsCount -  2843
Expected:  [0, 1840, 730, 73, 1]
Predicted: [0, 1420, 730, 73, 1]
tweetIdsCount -  2844
Expected:  [0, 730, 73, 80, 1519]
Predicted: [0, 730, 73, 80, 1420]
tweetIdsCount -  2845
Expected:  [0, 299, 730, 73, 1]
Predicted: [0, 1390, 730, 73, 1]
tweetIdsCount -  2846
Expected:  [0, 730, 1839, 1, 1841]
Predicted: [0, 730, 1420, 1, 1420]
tweetIdsCount -  2847
Expected:  [0, 730, 1839, 73, 142]
Predicted: [0, 730, 1420, 73, 142]
tweetIdsCount -  2848
Expected:  [0, 73, 1839, 794, 921]
Predicted: [0, 73, 1420, 794, 921]
tweetIdsCount -  2849
Expected:  [0, 73

Expected:  [734, 0, 73, 131, 102]
Predicted: [734, 0, 73, 131, 102]
tweetIdsCount -  2929
Expected:  [0, 1884, 730, 1, 30]
Predicted: [0, 1420, 730, 1, 30]
tweetIdsCount -  2930
Expected:  [0, 1519, 1599, 833, 16]
Predicted: [0, 1420, 1420, 833, 16]
tweetIdsCount -  2931
Expected:  [0, 730, 73, 1197, 1854]
Predicted: [0, 730, 73, 1417, 1420]
tweetIdsCount -  2932
Expected:  [0, 73, 299, 730, 1519]
Predicted: [0, 73, 1390, 730, 1420]
tweetIdsCount -  2933
Expected:  [1519, 0, 1599, 8, 73]
Predicted: [1420, 0, 1420, 8, 73]
tweetIdsCount -  2934
Expected:  [0, 730, 73, 1, 101]
Predicted: [0, 730, 73, 1, 101]
tweetIdsCount -  2935
Expected:  [0, 1885, 73, 266, 1886]
Predicted: [0, 1420, 73, 1420, 1420]
tweetIdsCount -  2936
Expected:  [0, 1886, 266, 1887, 730]
Predicted: [0, 1420, 1420, 1420, 730]
tweetIdsCount -  2937
Expected:  [0, 16, 73, 118, 1888]
Predicted: [0, 16, 73, 118, 1420]
tweetIdsCount -  2938
Expected:  [0, 73, 52, 1889, 132]
Predicted: [0, 73, 52, 1420, 132]
tweetIdsCount -

In [17]:
len(trendingTopicsAll)

1934

In [19]:
from tensorflow.keras.models import model_from_json

In [20]:
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model.h5")
print("Saved model to disk")

Saved model to disk


In [21]:
json_file = open('model.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights("model.h5")
print("Loaded model from disk")

W0117 23:59:24.137207 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling GlorotUniform.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
W0117 23:59:24.143220 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling Orthogonal.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
W0117 23:59:24.147231 15184 deprecation.py:506] From C:\Users\Mithila\Anaconda3\lib\site-packages\tensorflow\python\ops\init_ops.py:97: calling Zeros.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and

Loaded model from disk


In [22]:
loaded_model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

In [23]:
X, y = generate_data()
yhat = loaded_model.predict(X)
print('Expected:  %s' % one_hot_decode(y))
print('Predicted: %s' % one_hot_decode(yhat))

tweetIdsCount -  2990
Expected:  [0, 730, 73, 118, 81]
Predicted: [0, 730, 73, 118, 81]


In [24]:
def getTestData():
    for i in range(9):
        X, y = generate_data()
        yhat = loaded_model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))

In [25]:
getTestData()
print(testaccuracy)

tweetIdsCount -  2991
Expected:  [0, 1929, 730, 73, 1930]
Predicted: [0, 1420, 730, 73, 1420]
tweetIdsCount -  2992
Expected:  [0, 1931, 730, 73, 602]
Predicted: [0, 1420, 730, 73, 602]
tweetIdsCount -  2993
Expected:  [0, 730, 73, 1932, 1933]
Predicted: [0, 730, 73, 1420, 1420]
tweetIdsCount -  2994
Expected:  [0, 730, 36, 537, 95]
Predicted: [0, 730, 36, 1399, 95]
tweetIdsCount -  2995
Expected:  [0, 73, 730, 1447, 794]
Predicted: [0, 73, 730, 1420, 794]
tweetIdsCount -  2996
Expected:  [0, 1402, 730, 73, 1]
Predicted: [0, 1402, 730, 73, 1]
tweetIdsCount -  2997
Expected:  [0, 118, 494, 730, 73]
Predicted: [0, 118, 494, 730, 73]
tweetIdsCount -  2998
Expected:  [0, 73, 730, 134, 833]
Predicted: [0, 73, 730, 134, 833]
tweetIdsCount -  2999


IndexError: list index out of range